In [ ]:
!nvidia-smi -L
import psutil
print(psutil.virtual_memory())

lemodel = 'slon'
leartist = 'unknown'
legenre = 'unknown'
leeventlog = False

GPU 0: Tesla T4 (UUID: GPU-1d6551b6-262e-815d-1255-6b5128ef486c)
svmem(total=13617745920, available=12766134272, percent=6.3, used=600608768, free=10925678592, active=975699968, inactive=1472458752, buffers=115712000, cached=1975746560, shared=1241088, slab=136245248)


In [ ]:
 from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


<font color=purple size=5>💮 Setup 💮</font>

In [ ]:
!pip install git+https://github.com/openai/jukebox.git
!git clone https://github.com/openai/jukebox.git
!pip install av==8.1.0
!pip install tensorboardX 
import os

lemodelpath = '/content/gdrive/MyDrive/juke/' + lemodel + '_prior/checkpoint_latest.pth.tar'
leaudio_files_dir = '/content/gdrive/MyDrive/' + lemodel
lepriorname = lemodel + '_prior'

print(lemodelpath,leaudio_files_dir,lepriorname,os.path.isfile(lemodelpath))

############### To Change to Google Drive

fin = open("/usr/local/lib/python3.7/dist-packages/jukebox/utils/logger.py", "rt")
data = fin.read()
data = data.replace('logdir = f"{hps.local_logdir}/{hps.name}"', 'logdir = f"/content/gdrive/MyDrive/juke/{hps.name}"')
fin.close()
fin = open("/usr/local/lib/python3.7/dist-packages/jukebox/utils/logger.py", "wt")
fin.write(data)
fin.close()

############### To Sample with Google Drive

fin = open("/usr/local/lib/python3.7/dist-packages/jukebox/hparams.py", "rt")
data = fin.read()
fin.close()

data += lemodel + """_prior = Hyperparams()   
""" + lemodel + """_prior.update(prior_1b_lyrics)
""" + lemodel + """_prior.restore_prior='""" + lemodelpath + """'
""" + lemodel + """_prior.level=2
HPARAMS_REGISTRY['""" + lemodel + """_prior'] = """ + lemodel + """_prior
"""

#data = data.replace('y_bins=(10,100)','y_bins=(604, 7898)')
data = data.replace('min_duration=60.0','min_duration=24.0')
#data = data.replace('max_duration=600.0','max_duration=666.0')

fin = open("/usr/local/lib/python3.7/dist-packages/jukebox/hparams.py", "wt")
fin.write(data)
fin.close()

####################### To get Artist Genre, Lyrics 

fin = open("/usr/local/lib/python3.7/dist-packages/jukebox/data/files_dataset.py", "rt")
data = fin.read()
fin.close()

data = data.replace('def get_metadata(self, filename, test):','''def get_metadata(self, filename, test):
        lyr = ""
        letx = filename.replace('.wav','.txt').replace('.mp3','.txt')
        print(letx)
        if os.path.isfile(letx):
          fin = open(letx, "rt")
          lyr = fin.read()
          print('yes')
          fin.close''')

data = data.replace('return None, None, None',"return '" + leartist + "', '" + legenre + "', lyr")
data = data.replace('import librosa', '''import librosa
import os''')


fin = open("/usr/local/lib/python3.7/dist-packages/jukebox/data/files_dataset.py", "wt")
fin.write(data)
fin.close()

####################### step print

fin = open("/content/jukebox/jukebox/train.py", "rt")
data = fin.read()
fin.close()

data = data.replace('log_inputs(orig_model, logger, x_in, y, x_out, hps)','log_inputs(orig_model, logger, x_in, y, x_out, hps);print(colored("steps:" + str(logger.iters),"magenta"))')
data = """from termcolor import colored

""" + data

if leeventlog == False:
  data = data.replace('logger.flush()','#logger.flush()')
  
fin = open("/content/jukebox/jukebox/train.py", "wt")
fin.write(data)
fin.close()


fin = open("/usr/local/lib/python3.7/dist-packages/jukebox/make_models.py", "rt")
data = fin.read(); fin.close()  

data = data.replace("dist.barrier()","dist.barrier(); print('1')")
#data = data.replace("checkpoint = t.load(restore, map_location=t.device('cpu'))","checkpoint = t.load(restore, map_location=t.device('cuda')); print('2')")
data = data.replace(".format(restore))",".format(restore)); print(3); import gc; gc.collect()")

fin = open("/usr/local/lib/python3.7/dist-packages/jukebox/make_models.py", "wt")
fin.write(data); fin.close()  


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/openai/jukebox.git to /tmp/pip-req-build-h_njyndg
  Running command git clone -q https://github.com/openai/jukebox.git /tmp/pip-req-build-h_njyndg
     |████████████████████████████████| 60 kB 8.0 MB/s 
     |████████████████████████████████| 238 kB 2.5 MB/s 
     |████████████████████████████████| 3.5 MB 45.9 MB/s 
     |████████████████████████████████| 1.6 MB 55.6 MB/s 
     |████████████████████████████████| 2.5 MB 10.3 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 20.2 MB 1.2 MB/s 
  Created wheel for jukebox: filename=jukebox-1.0-py3-none-any.whl size=197916 sha256=a4b63eeb069c2a8404e81d288f7083cc035f56ab8a00f4eef04a4b2240840813
  Stored in directory: /tmp/pip-ephem-wheel-cache-ehxjqqzn/wheels/d6/42/39/91f8a32505a445499702ae0f8877

## Prior


In [ ]:
import gc; gc.collect()

lehps = ('vqvae,prior_1b_lyrics,all_fp16,cpu_ema','vqvae,prior_1b_lyrics,'+lepriorname+',all_fp16,cpu_ema')[os.path.isfile(lemodelpath)]
print(("new training model",lepriorname + " model found")[os.path.isfile(lemodelpath)])

!python jukebox/jukebox/train.py \
--prior --test --train --aug_shift --aug_blend \
--hps=$lehps \
--save_iters=238 \
--levels=3 \
--level=2 \
--name=$lepriorname \
--sample_length=786432     \
--bs=1 \
--audio_files_dir=$leaudio_files_dir  \
--weight_decay=0.01



Выходные данные были обрезаны до нескольких последних строк (5000).
 69% 4215/6144 [04:19<01:38, 19.57it/s]
 69% 4218/6144 [04:19<01:37, 19.80it/s]
 69% 4220/6144 [04:19<01:37, 19.83it/s]
 69% 4222/6144 [04:19<01:37, 19.68it/s]
 69% 4225/6144 [04:19<01:38, 19.55it/s]
 69% 4227/6144 [04:19<01:38, 19.45it/s]
 69% 4230/6144 [04:19<01:37, 19.69it/s]
 69% 4232/6144 [04:20<01:38, 19.35it/s]
 69% 4235/6144 [04:20<01:37, 19.64it/s]
 69% 4238/6144 [04:20<01:37, 19.60it/s]
 69% 4240/6144 [04:20<01:36, 19.68it/s]
 69% 4242/6144 [04:20<01:36, 19.75it/s]
 69% 4244/6144 [04:20<01:38, 19.28it/s]
 69% 4246/6144 [04:20<01:38, 19.18it/s]
 69% 4249/6144 [04:20<01:37, 19.47it/s]
 69% 4251/6144 [04:21<01:38, 19.23it/s]
 69% 4253/6144 [04:21<01:37, 19.44it/s]
 69% 4256/6144 [04:21<01:37, 19.30it/s]
 69% 4258/6144 [04:21<01:37, 19.39it/s]
 69% 4261/6144 [04:21<01:36, 19.48it/s]
 69% 4263/6144 [04:21<01:40, 18.63it/s]
 69% 4265/6144 [04:21<01:40, 18.65it/s]
 69% 4267/6144 [04:21<01:40, 18.72it/s]
 69% 4269/61

<font size=60> 🕴️‍♀️ </font>